## ROBERTA PIPELINE

In [ ]:
# Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
!pip install simpletransformers
from simpletransformers.classification import ClassificationModel, ClassificationArgs
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import f1_score, recall_score, precision_score
from sklearn.metrics import matthews_corrcoef

# Check GPU
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Sun Nov 13 10:18:46 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  A100-SXM4-40GB      Off  | 00000000:00:04.0 Off |                    0 |
| N/A   30C    P0    47W / 400W |      0MiB / 40536MiB |      0%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+-------------

In [ ]:
# Load the dataset from google drive
from google.colab import drive
drive.mount('/content/drive')

# Import downsampled dataset
df = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/DATASET_downsampled.xlsx')

# Import without google drive
# df = pd.read_excel('DATASET_downsampled.xlsx')

df = df.drop(columns = ['Unnamed: 0'])

df.info()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       2592 non-null   object
 1   kano_labels  2592 non-null   object
 2   labels       2592 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 60.9+ KB


In [ ]:
# Show the distribution of the labels
print(df['labels'].value_counts())

0    648
2    648
3    648
1    648
Name: labels, dtype: int64


In [ ]:
# Rename the columns so that simple transformers can handle them
train_data = df[['review','labels']]
train_data.columns = ['text', 'labels']
train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   text    2592 non-null   object
 1   labels  2592 non-null   int64 
dtypes: int64(1), object(1)
memory usage: 40.6+ KB


In [ ]:
# Model implementation and k-fold cross validation with Simpletransformers

# Wrapper function to calculate f1-score with additional parameters
def f1_multiclass(labels, preds):
    return f1_score(labels, preds, average = None)

# Wrapper function to calculate recall with additional parameters
def recall_multiclass(labels, preds):
    return recall_score(labels, preds, average = None)

# Wrapper function to calculate precision with additional parameters
def precision_multiclass(labels, preds):
    return precision_score(labels, preds, average = None)

# K-fold cross validation with 10 folds
n = 10
kf = KFold(n_splits=n, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc = []
resultsf1 = []
resultsPrecision = []
resultsRecall = []

model_args = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create the ClassificationModel
model = ClassificationModel(
    'roberta',
    'roberta-base',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf.split(train_data):
  train_df = train_data.iloc[train_index]
  val_df = train_data.iloc[val_index]

  model.train_model(train_df)
  result, model_outputs, wrong_predictions = model.eval_model(val_df, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)
  print(result)
  
  # Add scores to the respective lists
  resultsAcc.append(result['acc'])
  resultsf1.append(result['f1'])
  resultsPrecision.append(result['precision'])
  resultsRecall.append(result['recall'])

  print("results accuracy",resultsAcc)
  print(f"Mean-Precision: {sum(resultsAcc) / len(resultsAcc)}")
  print('results f1: ', resultsf1)
  print('results precision: ', resultsPrecision)
  print('results recall: ', resultsRecall)

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.decoder.weight', 'lm_head.dense.weight', 'roberta.pooler.dense.weight', 'lm_head.dense.bias', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.layer_norm.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifi

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/292 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/33 [00:00<?, ?it/s]

{'mcc': 0.684771884858165, 'f1': array([0.87769784, 0.75167785, 0.80733945, 0.60162602]), 'acc': 0.7615384615384615, 'recall': array([0.91044776, 0.8358209 , 0.70967742, 0.578125  ]), 'precision': array([0.84722222, 0.68292683, 0.93617021, 0.62711864]), 'eval_loss': 0.5973547155206854}
results accuracy [0.7615384615384615]
Mean-Precision: 0.7615384615384615
results f1:  [array([0.87769784, 0.75167785, 0.80733945, 0.60162602])]
results precision:  [array([0.84722222, 0.68292683, 0.93617021, 0.62711864])]
results recall:  [array([0.91044776, 0.8358209 , 0.70967742, 0.578125  ])]


...

{'mcc': 0.9948474228899725, 'f1': array([0.99280576, 1.        , 1.        , 0.99236641]), 'acc': 0.9961389961389961, 'recall': array([0.98571429, 1.        , 1.        , 1.        ]), 'precision': array([1.        , 1.        , 1.        , 0.98484848]), 'eval_loss': 0.014096922946698738}
results accuracy [0.7615384615384615, 0.823076923076923, 0.8764478764478765, 0.8687258687258688, 0.9498069498069498, 0.9575289575289575, 0.9652509652509652, 0.9768339768339769, 0.9961389961389961]
Mean-Precision: 0.9083721083721082
results f1:  [array([0.87769784, 0.75167785, 0.80733945, 0.60162602]), array([0.9047619 , 0.768     , 0.91666667, 0.688     ]), array([0.95867769, 0.84210526, 0.91056911, 0.80851064]), array([0.95798319, 0.81690141, 0.94488189, 0.76923077]), array([0.94573643, 0.96551724, 0.97297297, 0.91729323]), array([1.        , 0.93617021, 0.97014925, 0.92436975]), array([0.99300699, 0.94117647, 0.98275862, 0.94308943]), array([1.        , 0.95726496, 0.98630137, 0.96240602]), array([0

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/292 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/33 [00:00<?, ?it/s]

{'mcc': 0.9897496189362213, 'f1': array([0.99270073, 0.99259259, 1.        , 0.98461538]), 'acc': 0.9922779922779923, 'recall': array([1.        , 1.        , 1.        , 0.96969697]), 'precision': array([0.98550725, 0.98529412, 1.        , 1.        ]), 'eval_loss': 0.04490319059837158}
results accuracy [0.7615384615384615, 0.823076923076923, 0.8764478764478765, 0.8687258687258688, 0.9498069498069498, 0.9575289575289575, 0.9652509652509652, 0.9768339768339769, 0.9961389961389961, 0.9922779922779923]
Mean-Precision: 0.9167626967626967
results f1:  [array([0.87769784, 0.75167785, 0.80733945, 0.60162602]), array([0.9047619 , 0.768     , 0.91666667, 0.688     ]), array([0.95867769, 0.84210526, 0.91056911, 0.80851064]), array([0.95798319, 0.81690141, 0.94488189, 0.76923077]), array([0.94573643, 0.96551724, 0.97297297, 0.91729323]), array([1.        , 0.93617021, 0.97014925, 0.92436975]), array([0.99300699, 0.94117647, 0.98275862, 0.94308943]), array([1.        , 0.95726496, 0.98630137, 0.9

In [ ]:
print("results accuracy",resultsAcc)
print(f"Mean-accuracy: {sum(resultsAcc) / len(resultsAcc)}")
print('results f1: ', resultsf1)
print('results precision: ', resultsPrecision)
print('results recall: ', resultsRecall)

results accuracy [0.7615384615384615, 0.823076923076923, 0.8764478764478765, 0.8687258687258688, 0.9498069498069498, 0.9575289575289575, 0.9652509652509652, 0.9768339768339769, 0.9961389961389961, 0.9922779922779923]
results f1:  [array([0.87769784, 0.75167785, 0.80733945, 0.60162602]), array([0.9047619 , 0.768     , 0.91666667, 0.688     ]), array([0.95867769, 0.84210526, 0.91056911, 0.80851064]), array([0.95798319, 0.81690141, 0.94488189, 0.76923077]), array([0.94573643, 0.96551724, 0.97297297, 0.91729323]), array([1.        , 0.93617021, 0.97014925, 0.92436975]), array([0.99300699, 0.94117647, 0.98275862, 0.94308943]), array([1.        , 0.95726496, 0.98630137, 0.96240602]), array([0.99280576, 1.        , 1.        , 0.99236641]), array([0.99270073, 0.99259259, 1.        , 0.98461538])]
results precision:  [array([0.84722222, 0.68292683, 0.93617021, 0.62711864]), array([0.890625  , 0.8       , 0.91666667, 0.671875  ]), array([0.95081967, 0.82352941, 0.94915254, 0.8028169 ]), array([

In [ ]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

def PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1):

  np_resultsPrecision = np.array(resultsPrecision)
  np_resultsRecall = np.array(resultsRecall)
  np_resultsf1  = np.array(resultsf1)

  # Calculate the mean precision for each label
  df_resultsPrecision = pd.DataFrame(np_resultsPrecision, columns=list('BDIP'))
  precision_b_mean = df_resultsPrecision['B'].mean()
  precision_d_mean = df_resultsPrecision['D'].mean()
  precision_i_mean = df_resultsPrecision['I'].mean()
  precision_p_mean = df_resultsPrecision['P'].mean()

  # Calculate the mean recall for each label
  df_resultsRecall = pd.DataFrame(np_resultsRecall, columns=list('BDIP'))
  recall_b_mean = df_resultsRecall['B'].mean()
  recall_d_mean = df_resultsRecall['D'].mean()
  recall_i_mean = df_resultsRecall['I'].mean()
  recall_p_mean = df_resultsRecall['P'].mean()

  # Calculate the mean f1-score for each label
  df_resultsf1 = pd.DataFrame(np_resultsf1, columns=list('BDIP'))
  f1_b_mean = df_resultsf1['B'].mean()
  f1_d_mean = df_resultsf1['D'].mean()
  f1_i_mean = df_resultsf1['I'].mean()
  f1_p_mean = df_resultsf1['P'].mean()

  # Create dataframe with summarized results
  metrics = [{'B': precision_b_mean, 'D': precision_d_mean, 'I': precision_i_mean, 'P':precision_p_mean},
          {'B': recall_b_mean, 'D': recall_d_mean, 'I': recall_i_mean, 'P': recall_p_mean},
          {'B': f1_b_mean, 'D': f1_d_mean, 'I': f1_i_mean, 'P': f1_p_mean} ]
  train_df_metrics = pd.DataFrame(metrics, index=['Average precision',
                                'Average recall',
                                'Average F1-Score'])
  return train_df_metrics

PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1)

B         D         I         P
Average precision  0.960853  0.880799  0.970446  0.864077
Average recall     0.964254  0.916684  0.931459  0.855284
Average F1-Score   0.962337  0.897141  0.949164  0.859151

## Training on the dataset at hand, testing on the 'Trainingskorpus' dataset

In [ ]:
# Import of 'Trainingskorpus_Final', which gives the final labeling
testset1 = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/Trainingskorpus_Final.xlsx')

# Import without google drive
# testset1 = pd.read_excel('Trainingskorpus_Final.xlsx')

testset1 = testset1.drop(columns = ['Unnamed: 0'])
testset1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
dtypes: object(2)
memory usage: 25.5+ KB


In [ ]:
# Show the distribution of the labels
print(testset1['kano_labels'].value_counts())

B    1102
P     395
D      95
I      30
Name: kano_labels, dtype: int64


In [ ]:
# Import of 'Trainingskorpus_InitialLabels', which gives the initial labeling of two sometimes differing labels
testset2 = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/Trainingskorpus_InitialLabels.xlsx')

# Import without google drive
# testset2 = pd.read_excel('Trainingskorpus_InitialLabels.xlsx')

testset2 = testset2.drop(columns = ['Unnamed: 0'])
testset2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   review   1622 non-null   object
 1   label 1  1622 non-null   object
 2   label 2  1622 non-null   object
dtypes: object(3)
memory usage: 38.1+ KB


In [ ]:
# Merge the two sets so we have the final labels as well as the initial labels in the testset
testset = testset1.merge(testset2, left_on='review', right_on='review')
testset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1622 entries, 0 to 1621
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
 2   label 1      1622 non-null   object
 3   label 2      1622 non-null   object
dtypes: object(4)
memory usage: 63.4+ KB


In [ ]:
# Add a column 'equal' which is True if the two initial labels are equal and false otherwise

equal = [None]*np.size(testset['review'])

i = 0
for label1, label2 in zip(testset2['label 1'], testset2['label 2']):
  if(label1 == label2):
    equal[i] = True
  else:
    equal[i] = False
  i += 1
  
testset['equal'] = equal

In [ ]:
# Calculate the accuracy of the whole testset as well as 
# only the parts where the inital two labels are equal (accuracy_clear)
# or differ (accuracy_diff)

accuracy_clear = 0.
accuracy_diff = 0.
n_clear = 0
n_diff = 0
all_predicted_labels = []
predicted_labels_equal_initial_label = []
predicted_labels_diff_initial_label = []
true_label_equal = []
true_label_diff = []

for label, review, equal in zip(testset['kano_labels'],  testset['review'], testset['equal']):
  
  test_prediction, raw_outputs = model.predict([review])
  
  predicted_label = ''

  if test_prediction[0] == 0:
    predicted_label = 'B'
  if test_prediction[0] == 1:
    predicted_label = 'D'
  if test_prediction[0] == 2:
    predicted_label = 'I'
  if test_prediction[0] == 3:
    predicted_label = 'P'

  all_predicted_labels.append(predicted_label)
  
  if equal:
    n_clear += 1
    predicted_labels_equal_initial_label.append(predicted_label)
    true_label_equal.append(label)
    if label == predicted_label:
      accuracy_clear += 1.

  if not equal:
    n_diff += 1
    predicted_labels_diff_initial_label.append(predicted_label)
    true_label_diff.append(label)
    if label == predicted_label:
      accuracy_diff += 1.

accuracy = (accuracy_clear + accuracy_diff) / (n_clear + n_diff)

accuracy_clear /= n_clear
accuracy_diff /= n_diff

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
print('Accuracy Trainingskorpus:                                                  ', round(accuracy*100, 2), '%,  n =', (n_clear + n_diff))
print('Accuracy Trainingskorpus only on the data that coincides on initial labels:', round(accuracy_clear*100, 2), '%,  n =', n_clear)
print('Accuracy Trainingskorpus only on the data that differs on initial labels:  ', round(accuracy_diff*100, 2), '%,  n = ', n_diff)

Accuracy Trainingskorpus:                                                   71.76 %,  n = 1622
Accuracy Trainingskorpus only on the data that coincides on initial labels: 72.16 %,  n = 1383
Accuracy Trainingskorpus only on the data that differs on initial labels:   69.46 %,  n =  239


In [ ]:
# Calculate precision, recall and f1-score for each label

test_df_metrics = precision_recall_fscore_support(testset['kano_labels'], all_predicted_labels, average=None,labels=['B', 'D', 'I', 'P'])

print('Precision B: ', test_df_metrics[0][0])
print('Precision D: ', test_df_metrics[0][1])
print('Precision I: ', test_df_metrics[0][2])
print('Precision P: ', test_df_metrics[0][3])

print('Recall B: ', test_df_metrics[1][0])
print('Recall D: ', test_df_metrics[1][1])
print('Recall I: ', test_df_metrics[1][2])
print('Recall P: ', test_df_metrics[1][3])

print('F1-score B: ', test_df_metrics[2][0])
print('F1-score D: ', test_df_metrics[2][1])
print('F1-score I: ', test_df_metrics[2][2])
print('F1-score P: ', test_df_metrics[2][3])

Precision B:  0.8862944162436548
Precision D:  0.3719806763285024
Precision I:  1.0
Precision P:  0.49295774647887325
Recall B:  0.7921960072595281
Recall D:  0.8105263157894737
Recall I:  0.13333333333333333
Recall P:  0.5316455696202531
F1-score B:  0.8366075706756109
F1-score D:  0.509933774834437
F1-score I:  0.23529411764705882
F1-score P:  0.5115712545676004


In [ ]:
# Calculates the phi-coefficient for labels where both researchers agreed vs. where they disagreed

print('MCC for labels where both researchers agreed: ',matthews_corrcoef(true_label_equal, predicted_labels_equal_initial_label))
print('MCC for labels where both researchers disagreed: ',matthews_corrcoef(true_label_diff, predicted_labels_diff_initial_label))

MCC for labels where both researchers agreed:  0.4636555946990991
MCC for labels where both researchers disagreed:  0.43081770207091413


## Combine dataset at hand and 'Trainingskorpus' dataset, then do Train-Test-Split

In [ ]:
# Import combined downsampled dataset 
df_combined = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/DATASET_Trainingskorpus_combined.xlsx')
df_combined = df_combined.drop(columns = ['Unnamed: 0'])

# Import without google drive
# df_combined = pd.read_excel('DATASET_Trainingskorpus_combined.xlsx')

# Rename column so that simple transformers can handle it
df_combined = df_combined.rename(columns = {'review': 'text'})
df_combined.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2972 entries, 0 to 2971
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   text         2972 non-null   object
 1   kano_labels  2972 non-null   object
 2   labels       2972 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 69.8+ KB


In [ ]:
# Show the distribution of the labels
print(df_combined['labels'].value_counts())

2    743
3    743
1    743
0    743
Name: labels, dtype: int64


In [ ]:
# 10-fold cross validation on the combined dataset

n2 = 10
kf2 = KFold(n_splits=n2, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc2 = []
resultsf12 = []
resultsPrecision2 = []
resultsRecall2 = []

model_args2 = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create a ClassificationModel
model2 = ClassificationModel(
    'roberta',
    'roberta-base',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf2.split(df_combined):
  train_df2 = df_combined.iloc[train_index]
  val_df2 = df_combined.iloc[val_index]

  model2.train_model(df_combined)
  result2, model_outputs2, wrong_predictions2 = model2.eval_model(val_df2, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)

  print(result2)
  # Add scores to the respective lists
  resultsAcc2.append(result2['acc'])
  resultsf12.append(result2['f1'])
  resultsPrecision2.append(result2['precision'])
  resultsRecall2.append(result2['recall'])

  print("results accuracy",resultsAcc2)
  print(f"Mean-accuracy: {sum(resultsAcc2) / len(resultsAcc2)}")
  print('results f1: ', resultsf12)
  print('results precision: ', resultsPrecision2)
  print('results recall: ', resultsRecall2)


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.decoder.weight', 'lm_head.dense.weight', 'roberta.pooler.dense.weight', 'lm_head.dense.bias', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.layer_norm.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifi

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

{'mcc': 0.7741390564921455, 'f1': array([0.92307692, 0.79487179, 0.89552239, 0.66129032]), 'acc': 0.8288590604026845, 'recall': array([0.96551724, 0.87323944, 0.86956522, 0.57746479]), 'precision': array([0.88421053, 0.72941176, 0.92307692, 0.77358491]), 'eval_loss': 0.44267960598594264}
results accuracy [0.8288590604026845]
Mean-Precision: 0.8288590604026845
results f1:  [array([0.92307692, 0.79487179, 0.89552239, 0.66129032])]
results precision:  [array([0.88421053, 0.72941176, 0.92307692, 0.77358491])]
results recall:  [array([0.96551724, 0.87323944, 0.86956522, 0.57746479])]


...

{'mcc': 0.9910231199387626, 'f1': array([0.992     , 0.99363057, 0.99328859, 0.99386503]), 'acc': 0.9932659932659933, 'recall': array([1.        , 1.        , 0.98666667, 0.98780488]), 'precision': array([0.98412698, 0.98734177, 1.        , 1.        ]), 'eval_loss': 0.026789518171235135}
results accuracy [0.8288590604026845, 0.8624161073825504, 0.9461279461279462, 0.9461279461279462, 0.9595959595959596, 0.9797979797979798, 0.9797979797979798, 0.9932659932659933, 0.9932659932659933]
Mean-Precision: 0.9432505517516704
results f1:  [array([0.92307692, 0.79487179, 0.89552239, 0.66129032]), array([0.89855072, 0.84393064, 0.94339623, 0.74603175]), array([0.98013245, 0.93167702, 0.97986577, 0.88721805]), array([0.9875    , 0.89256198, 0.98224852, 0.90277778]), array([0.98461538, 0.94478528, 0.95652174, 0.95705521]), array([0.98701299, 0.96598639, 0.99354839, 0.97101449]), array([0.99328859, 0.98089172, 0.97744361, 0.96774194]), array([1.        , 0.99337748, 0.99371069, 0.98571429]), array([

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

{'mcc': 0.9822462064306674, 'f1': array([1.        , 0.97222222, 1.        , 0.97333333]), 'acc': 0.9865319865319865, 'recall': array([1.        , 1.        , 1.        , 0.94805195]), 'precision': array([1.        , 0.94594595, 1.        , 1.        ]), 'eval_loss': 0.05451166237655439}
results accuracy [0.8288590604026845, 0.8624161073825504, 0.9461279461279462, 0.9461279461279462, 0.9595959595959596, 0.9797979797979798, 0.9797979797979798, 0.9932659932659933, 0.9932659932659933, 0.9865319865319865]
Mean-Precision: 0.947578695229702
results f1:  [array([0.92307692, 0.79487179, 0.89552239, 0.66129032]), array([0.89855072, 0.84393064, 0.94339623, 0.74603175]), array([0.98013245, 0.93167702, 0.97986577, 0.88721805]), array([0.9875    , 0.89256198, 0.98224852, 0.90277778]), array([0.98461538, 0.94478528, 0.95652174, 0.95705521]), array([0.98701299, 0.96598639, 0.99354839, 0.97101449]), array([0.99328859, 0.98089172, 0.97744361, 0.96774194]), array([1.        , 0.99337748, 0.99371069, 0.9

In [ ]:
print("results accuracy",resultsAcc2)
print(f"Mean-accuracy: {sum(resultsAcc) / len(resultsAcc)}")
print('results f1: ', resultsf12)
print('results precision: ', resultsPrecision2)
print('results recall: ', resultsRecall2)

results accuracy [0.8288590604026845, 0.8624161073825504, 0.9461279461279462, 0.9461279461279462, 0.9595959595959596, 0.9797979797979798, 0.9797979797979798, 0.9932659932659933, 0.9932659932659933, 0.9865319865319865]
results f1:  [array([0.92307692, 0.79487179, 0.89552239, 0.66129032]), array([0.89855072, 0.84393064, 0.94339623, 0.74603175]), array([0.98013245, 0.93167702, 0.97986577, 0.88721805]), array([0.9875    , 0.89256198, 0.98224852, 0.90277778]), array([0.98461538, 0.94478528, 0.95652174, 0.95705521]), array([0.98701299, 0.96598639, 0.99354839, 0.97101449]), array([0.99328859, 0.98089172, 0.97744361, 0.96774194]), array([1.        , 0.99337748, 0.99371069, 0.98571429]), array([0.992     , 0.99363057, 0.99328859, 0.99386503]), array([1.        , 0.97222222, 1.        , 0.97333333])]
results precision:  [array([0.88421053, 0.72941176, 0.92307692, 0.77358491]), array([0.88571429, 0.81111111, 0.9375    , 0.81034483]), array([0.98666667, 0.90361446, 0.97333333, 0.921875  ]), array(

In [ ]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

PrecisionRecallF1Table(resultsPrecision2, resultsRecall2, resultsf12)

B         D         I         P
Average precision  0.967274  0.907329  0.976473  0.937091
Average recall     0.982465  0.957892  0.967016  0.876723
Average F1-Score   0.974618  0.931394  0.971555  0.904604